-------------------------------------------

### Importing needed packages

In [89]:
import os, json
import requests
import pandas as pd
import geopandas as gpd
%config Completer.use_jedi = False
from geopy.geocoders import Nominatim

### Obtaining Restaurant Data from the Wyre Data Api

In [9]:
url = "https://wyre-data.p.rapidapi.com/restaurants/town/london"
headers = {
"X-RapidAPI-Key": "bef0d5394emsh967f44a929b6eefp15f2e8jsn801a23ddca00",
"X-RapidAPI-Host": "wyre-data.p.rapidapi.com"
}

response = requests.request("GET", url, headers=headers)
print(response.text)

[{"_id":"620cd586aa28c13b79512f6f","BusinessName":"101 Thai Kitchen","RatingValue":"3","AddressLine2":"London","PostCode":"W6 0RX","Geocode_Longitude":-0.244311,"Geocode_Latitude":51.493618},{"_id":"620cd586aa28c13b79512f75","BusinessName":"2020 Mezza & Grill","RatingValue":"AwaitingInspection","AddressLine2":"London","PostCode":"W6 9PL","Geocode_Longitude":-0.222939,"Geocode_Latitude":51.488278},{"_id":"620cd586aa28c13b79512f78","BusinessName":"222 Vegan Restaurant","RatingValue":"3","AddressLine2":"London","PostCode":"W14 9NU","Geocode_Longitude":-0.202997,"Geocode_Latitude":51.485879},{"_id":"620cd586aa28c13b79512f7b","BusinessName":"24 / 7 Supermarket","RatingValue":"3","AddressLine2":"London","PostCode":"W6 0QU","Geocode_Longitude":-0.232831,"Geocode_Latitude":51.492834},{"_id":"620cd586aa28c13b79512f7e","BusinessName":"696 Mangal","RatingValue":"5","AddressLine2":"London","PostCode":"SW6 5SA","Geocode_Longitude":-0.206834,"Geocode_Latitude":51.474724},{"_id":"620cd586aa28c13b7951

In [24]:
print(len(response.text))
#response.json()
json.loads(response.text)[:]

[{'_id': '620cd586aa28c13b79512f6f',
  'BusinessName': '101 Thai Kitchen',
  'RatingValue': '3',
  'AddressLine2': 'London',
  'PostCode': 'W6 0RX',
  'Geocode_Longitude': -0.244311,
  'Geocode_Latitude': 51.493618},
 {'_id': '620cd586aa28c13b79512f75',
  'BusinessName': '2020 Mezza & Grill',
  'RatingValue': 'AwaitingInspection',
  'AddressLine2': 'London',
  'PostCode': 'W6 9PL',
  'Geocode_Longitude': -0.222939,
  'Geocode_Latitude': 51.488278},
 {'_id': '620cd586aa28c13b79512f78',
  'BusinessName': '222 Vegan Restaurant',
  'RatingValue': '3',
  'AddressLine2': 'London',
  'PostCode': 'W14 9NU',
  'Geocode_Longitude': -0.202997,
  'Geocode_Latitude': 51.485879},
 {'_id': '620cd586aa28c13b79512f7b',
  'BusinessName': '24 / 7 Supermarket',
  'RatingValue': '3',
  'AddressLine2': 'London',
  'PostCode': 'W6 0QU',
  'Geocode_Longitude': -0.232831,
  'Geocode_Latitude': 51.492834},
 {'_id': '620cd586aa28c13b79512f7e',
  'BusinessName': '696 Mangal',
  'RatingValue': '5',
  'AddressLine2

### Converting the Json data from the api into a pandas dataframe

In [28]:
rdata = pd.DataFrame(response.json())
rdata.head()

_id          BusinessName         RatingValue  \
0  620cd586aa28c13b79512f6f      101 Thai Kitchen                   3   
1  620cd586aa28c13b79512f75    2020 Mezza & Grill  AwaitingInspection   
2  620cd586aa28c13b79512f78  222 Vegan Restaurant                   3   
3  620cd586aa28c13b79512f7b    24 / 7 Supermarket                   3   
4  620cd586aa28c13b79512f7e            696 Mangal                   5   

  AddressLine2 PostCode  Geocode_Longitude  Geocode_Latitude AddressLine3  
0       London   W6 0RX          -0.244311         51.493618          NaN  
1       London   W6 9PL          -0.222939         51.488278          NaN  
2       London  W14 9NU          -0.202997         51.485879          NaN  
3       London   W6 0QU          -0.232831         51.492834          NaN  
4       London  SW6 5SA          -0.206834         51.474724          NaN

In [29]:
rdata.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 22565 entries, 0 to 22564
Data columns (total 8 columns):
 #   Column             Non-Null Count  Dtype  
---  ------             --------------  -----  
 0   _id                22565 non-null  object 
 1   BusinessName       22565 non-null  object 
 2   RatingValue        22565 non-null  object 
 3   AddressLine2       22557 non-null  object 
 4   PostCode           22539 non-null  object 
 5   Geocode_Longitude  22033 non-null  float64
 6   Geocode_Latitude   22033 non-null  float64
 7   AddressLine3       21579 non-null  object 
dtypes: float64(2), object(6)
memory usage: 1.4+ MB


In [39]:
#len(rdata)
print(f"There are {len(rdata[rdata['Geocode_Longitude'].isnull()])} rows of data, i.e. restaurants that have no Geocode_Longitude and Geocode_Latitude entries")

There are 532 rows of data, i.e. restaurants that have no Geocode_Longitude and Geocode_Latitude entries  


The rows just below, don't have any location information at all and will be dropped!

In [62]:
#print(532+22033 == len(rdata))
rows_to_drop = rdata[rdata['Geocode_Longitude'].isnull()][rdata[rdata['Geocode_Longitude'].isnull()]['PostCode'].isnull()].index
print(len(rows_to_drop))

0


There is also other data present that doesnt have lat, lon and has empty strings as postcodes. They will also be removed from the dataframe

In [129]:
index_to_drop2 = rdata[rdata['Geocode_Longitude'].isnull()][rdata[rdata['Geocode_Longitude'].isnull()]['PostCode']==''].index

print(f'Before dropping rows of data, len(rdata): {len(rdata)}', '\n')
#rdata = rdata.drop([i for i in rows_to_drop], axis=0)
print(f'After dropping rows of data, len(rdata): {len(rdata)}')

In [130]:
print(f'Before dropping rows of data, len(rdata): {len(rdata)}', '\n')
rdata = rdata.drop([i for i in index_to_drop2], axis=0)
print(f'After dropping rows of data, len(rdata): {len(rdata)}')

Before dropping rows of data, len(rdata): 22561 

After dropping rows of data, len(rdata): 22420


In [131]:
#reset index
rdata.reset_index(drop=True)
rdata.head()

_id          BusinessName         RatingValue  \
0  620cd586aa28c13b79512f6f      101 Thai Kitchen                   3   
1  620cd586aa28c13b79512f75    2020 Mezza & Grill  AwaitingInspection   
2  620cd586aa28c13b79512f78  222 Vegan Restaurant                   3   
3  620cd586aa28c13b79512f7b    24 / 7 Supermarket                   3   
4  620cd586aa28c13b79512f7e            696 Mangal                   5   

  AddressLine2 PostCode  Geocode_Longitude  Geocode_Latitude AddressLine3  
0       London   W6 0RX          -0.244311         51.493618          NaN  
1       London   W6 9PL          -0.222939         51.488278          NaN  
2       London  W14 9NU          -0.202997         51.485879          NaN  
3       London   W6 0QU          -0.232831         51.492834          NaN  
4       London  SW6 5SA          -0.206834         51.474724          NaN

Going back to geocode all restaurants which dont have long, lat but have postcodes

In [132]:
rdata.columns

Index(['_id', 'BusinessName', 'RatingValue', 'AddressLine2', 'PostCode',
       'Geocode_Longitude', 'Geocode_Latitude', 'AddressLine3'],
      dtype='object')

In [133]:
print(f"There are {len(rdata[rdata['Geocode_Latitude'].isnull()])} restaurants that we have to geocode")
rdata_geonull = rdata[rdata['Geocode_Latitude'].isnull()]
rdata_geonull

There are 387 restaurants that we have to geocode


_id                          BusinessName  \
78     620cd586aa28c13b7951316a                   Baxterstorey UK Ltd   
139    620cd586aa28c13b79513296                            Brown Rice   
187    620cd586aa28c13b795133b3                        Chapter Coffee   
454    620cd587aa28c13b795137a6                        Harris & Hoole   
610    620cd587aa28c13b79513b0f              Mariva Catering Services   
...                         ...                                   ...   
22513  620cd5a7aa28c13b7953153c                      Sportsman Casino   
22530  620cd5a7aa28c13b795315b1                     St Marys Hospital   
22549  620cd5a7aa28c13b79531683                        Sticks'n'Sushi   
22552  620cd5a7aa28c13b795316e2                 Summertons Of Mayfair   
22560  620cd5a7aa28c13b79531733  Sushi Gourmet At Sainsbury's Pimlico   

              RatingValue             AddressLine2  PostCode  \
78                      5                   London   SW6 2GD   
139                     5                   London    W6 9JG   
187                     5                   London   W14 8XU   
454                     5                   London   SW6 2FG   
610                     5                   London   SW6 2FR   
...                   ...                      ...       ...   
22513                   5  14-22 Old Quebec Street   W1H 7AR   
22530                   5          Winsland Street    W2 1HW   
22549  AwaitingInspection      City Of Westminster  SW1E 5DJ   
22552  AwaitingInspection          115 Park Street   W1K 7DY   
22560                   5           99 Wilton Road  SW1V 1LL   

       Geocode_Longitude  Geocode_Latitude AddressLine3  
78                   NaN               NaN          NaN  
139                  NaN               NaN          NaN  
187                  NaN               NaN          NaN  
454                  NaN               NaN          NaN  
610                  NaN               NaN          NaN  
...                  ...               ...          ...  
22513                NaN               NaN       London  
22530                NaN               NaN       London  
22549                NaN               NaN       London  
22552                NaN               NaN       London  
22560                NaN               NaN       London  

[387 rows x 8 columns]

In [134]:
rdata_geonull

_id                          BusinessName  \
78     620cd586aa28c13b7951316a                   Baxterstorey UK Ltd   
139    620cd586aa28c13b79513296                            Brown Rice   
187    620cd586aa28c13b795133b3                        Chapter Coffee   
454    620cd587aa28c13b795137a6                        Harris & Hoole   
610    620cd587aa28c13b79513b0f              Mariva Catering Services   
...                         ...                                   ...   
22513  620cd5a7aa28c13b7953153c                      Sportsman Casino   
22530  620cd5a7aa28c13b795315b1                     St Marys Hospital   
22549  620cd5a7aa28c13b79531683                        Sticks'n'Sushi   
22552  620cd5a7aa28c13b795316e2                 Summertons Of Mayfair   
22560  620cd5a7aa28c13b79531733  Sushi Gourmet At Sainsbury's Pimlico   

              RatingValue             AddressLine2  PostCode  \
78                      5                   London   SW6 2GD   
139                     5                   London    W6 9JG   
187                     5                   London   W14 8XU   
454                     5                   London   SW6 2FG   
610                     5                   London   SW6 2FR   
...                   ...                      ...       ...   
22513                   5  14-22 Old Quebec Street   W1H 7AR   
22530                   5          Winsland Street    W2 1HW   
22549  AwaitingInspection      City Of Westminster  SW1E 5DJ   
22552  AwaitingInspection          115 Park Street   W1K 7DY   
22560                   5           99 Wilton Road  SW1V 1LL   

       Geocode_Longitude  Geocode_Latitude AddressLine3  
78                   NaN               NaN          NaN  
139                  NaN               NaN          NaN  
187                  NaN               NaN          NaN  
454                  NaN               NaN          NaN  
610                  NaN               NaN          NaN  
...                  ...               ...          ...  
22513                NaN               NaN       London  
22530                NaN               NaN       London  
22549                NaN               NaN       London  
22552                NaN               NaN       London  
22560                NaN               NaN       London  

[387 rows x 8 columns]

### Geocoding postcodes...

In [ ]:
geolocator = Nominatim(timeout=10, user_agent="PDS")
geolocator

In [138]:
rdata_geonull['geocode'] = rdata_geonull['PostCode'].apply(geolocator.geocode, addressdetails=True)
rdata_geonull['geocode']

n:\development\geospatial\lib\site-packages\ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  """Entry point for launching an IPython kernel.


78           (SW6 2GD, (51.46750555, -0.1872712484691929))
139      (London Borough of Hammersmith and Fulham, Lon...
187      (London Borough of Hammersmith and Fulham, Lon...
454                        (SW6 2FG, (51.47412, -0.18297))
610      (London Borough of Hammersmith and Fulham, Lon...
                               ...                        
22513                                                 None
22530                                                 None
22549    (City of Westminster, Greater London, England,...
22552                                                 None
22560                                                 None
Name: geocode, Length: 387, dtype: object

In [141]:
rdata_geonull

_id                          BusinessName  \
78     620cd586aa28c13b7951316a                   Baxterstorey UK Ltd   
139    620cd586aa28c13b79513296                            Brown Rice   
187    620cd586aa28c13b795133b3                        Chapter Coffee   
454    620cd587aa28c13b795137a6                        Harris & Hoole   
610    620cd587aa28c13b79513b0f              Mariva Catering Services   
...                         ...                                   ...   
22513  620cd5a7aa28c13b7953153c                      Sportsman Casino   
22530  620cd5a7aa28c13b795315b1                     St Marys Hospital   
22549  620cd5a7aa28c13b79531683                        Sticks'n'Sushi   
22552  620cd5a7aa28c13b795316e2                 Summertons Of Mayfair   
22560  620cd5a7aa28c13b79531733  Sushi Gourmet At Sainsbury's Pimlico   

              RatingValue             AddressLine2  PostCode  \
78                      5                   London   SW6 2GD   
139                     5                   London    W6 9JG   
187                     5                   London   W14 8XU   
454                     5                   London   SW6 2FG   
610                     5                   London   SW6 2FR   
...                   ...                      ...       ...   
22513                   5  14-22 Old Quebec Street   W1H 7AR   
22530                   5          Winsland Street    W2 1HW   
22549  AwaitingInspection      City Of Westminster  SW1E 5DJ   
22552  AwaitingInspection          115 Park Street   W1K 7DY   
22560                   5           99 Wilton Road  SW1V 1LL   

       Geocode_Longitude  Geocode_Latitude AddressLine3  \
78                   NaN               NaN          NaN   
139                  NaN               NaN          NaN   
187                  NaN               NaN          NaN   
454                  NaN               NaN          NaN   
610                  NaN               NaN          NaN   
...                  ...               ...          ...   
22513                NaN               NaN       London   
22530                NaN               NaN       London   
22549                NaN               NaN       London   
22552                NaN               NaN       London   
22560                NaN               NaN       London   

                                                 geocode  
78         (SW6 2GD, (51.46750555, -0.1872712484691929))  
139    (London Borough of Hammersmith and Fulham, Lon...  
187    (London Borough of Hammersmith and Fulham, Lon...  
454                      (SW6 2FG, (51.47412, -0.18297))  
610    (London Borough of Hammersmith and Fulham, Lon...  
...                                                  ...  
22513                                               None  
22530                                               None  
22549  (City of Westminster, Greater London, England,...  
22552                                               None  
22560                                               None  

[387 rows x 9 columns]

The geocoder couldn't geocode all postcodes so rows with geocoded postcodes as 'None' must be deleted

In [241]:
rdata_geonull['geocode'] 

78           (SW6 2GD, (51.46750555, -0.1872712484691929))
139      (London Borough of Hammersmith and Fulham, Lon...
187      (London Borough of Hammersmith and Fulham, Lon...
454                        (SW6 2FG, (51.47412, -0.18297))
610      (London Borough of Hammersmith and Fulham, Lon...
                               ...                        
22513                                                 None
22530                                                 None
22549    (City of Westminster, Greater London, England,...
22552                                                 None
22560                                                 None
Name: geocode, Length: 387, dtype: object

isinstance(rdata_geonull.loc[[22560]]['geocode'][22560], type(None))

In [266]:
mixed_list = [i for i in rdata_geonull[['_id', 'geocode']].iterrows()]
print(len(mixed_list), '-----------\n')
none_index = [] #this list will store all indexes which have None as their geocoded address

for entry in mixed_list:
    if isinstance(entry[1]['geocode'], type(None)):
        print(f"Geocoded entry is {entry[1]['geocode']}, and index will be saved...")
        none_index.append(entry[0])
len(none_index)    

387 -----------

Geocoded entry is None, and index will be saved...
Geocoded entry is None, and index will be saved...
Geocoded entry is None, and index will be saved...
Geocoded entry is None, and index will be saved...
Geocoded entry is None, and index will be saved...
Geocoded entry is None, and index will be saved...
Geocoded entry is None, and index will be saved...
Geocoded entry is None, and index will be saved...
Geocoded entry is None, and index will be saved...
Geocoded entry is None, and index will be saved...
Geocoded entry is None, and index will be saved...
Geocoded entry is None, and index will be saved...
Geocoded entry is None, and index will be saved...
Geocoded entry is None, and index will be saved...
Geocoded entry is None, and index will be saved...
Geocoded entry is None, and index will be saved...
Geocoded entry is None, and index will be saved...
Geocoded entry is None, and index will be saved...
Geocoded entry is None, and index will be saved...
Geocoded entry

132

In [272]:
#deleting all rows of data in rdata(the original) that have index in none_index
rdata = rdata.drop([i for i in none_index], axis=0)

KeyError: '[ 1011  2103  2572  3261  3918  4231  4259  4664  4962  5145  5319  6357\n  6416  6427  6536  6642  6871  6922  6931  6953  7084  7136  7220  7230\n  7278  7300  7386  7421  7474  7513  7559  7688  8177  8343  8354  8393\n  8603  8633  8655  8683  8939  9057  9087  9207  9208  9249  9256  9324\n  9499  9504  9587  9617  9651  9657  9672  9709  9749  9824  9866  9888\n  9895  9932 10694 10927 11013 11415 11422 11862 12530 12847 13551 13553\n 13598 13703 13801 13975 14153 14528 14975 14988 15057 15537 15601 15654\n 15707 15726 16076 16837 17443 17481 18091 18123 18331 18373 18992 19086\n 19253 19718 20004 20064 20101 20138 20178 20403 20518 20565 20639 20664\n 20715 20939 21072 21159 21319 21493 21592 21797 21864 21902 21921 21992\n 22029 22044 22051 22117 22215 22289 22438 22448 22513 22530 22552 22560] not found in axis'

In [273]:
rdata

_id               BusinessName  \
0      620cd586aa28c13b79512f6f           101 Thai Kitchen   
1      620cd586aa28c13b79512f75         2020 Mezza & Grill   
2      620cd586aa28c13b79512f78       222 Vegan Restaurant   
3      620cd586aa28c13b79512f7b         24 / 7 Supermarket   
4      620cd586aa28c13b79512f7e                 696 Mangal   
...                         ...                        ...   
22559  620cd5a7aa28c13b7953172a                Sushi Daily   
22561  620cd5a7aa28c13b79531736                 Sushi Moka   
22562  620cd5a7aa28c13b79531739  Sushi Samba Covent Garden   
22563  620cd5a7aa28c13b79531766                  TAB X TAB   
22564  620cd5a7aa28c13b79531775                     Taj 51   

              RatingValue               AddressLine2  PostCode  \
0                       3                     London    W6 0RX   
1      AwaitingInspection                     London    W6 9PL   
2                       3                     London   W14 9NU   
3                       3                     London    W6 0QU   
4                       5                     London   SW6 5SA   
...                   ...                        ...       ...   
22559                   5     168 - 176 Edgware Road             
22561  AwaitingInspection  139 - 151 Marylebone Road   NW1 5QE   
22562                   5              Covent Garden  WC2E 8RF   
22563                   4     14-16 Westbourne Grove    W2 5RH   
22564                   5      41-54 Buckingham Gate  SW1E 6AF   

       Geocode_Longitude  Geocode_Latitude AddressLine3  
0              -0.244311         51.493618          NaN  
1              -0.222939         51.488278          NaN  
2              -0.202997         51.485879          NaN  
3              -0.232831         51.492834          NaN  
4              -0.206834         51.474724          NaN  
...                  ...               ...          ...  
22559          -0.252035         51.588065       London  
22561          -0.162473         51.520962       London  
22562          -0.122977         51.512071       London  
22563          -0.190147         51.515778       London  
22564          -0.137481         51.498480       London  

[22288 rows x 8 columns]

In [274]:
#deleting all rows of data in rdata(the original) that have index in none_index
rdata_geonull = rdata_geonull.drop([i for i in none_index], axis=0)
rdata_geonull

_id              BusinessName         RatingValue  \
78     620cd586aa28c13b7951316a       Baxterstorey UK Ltd                   5   
139    620cd586aa28c13b79513296                Brown Rice                   5   
187    620cd586aa28c13b795133b3            Chapter Coffee                   5   
454    620cd587aa28c13b795137a6            Harris & Hoole                   5   
610    620cd587aa28c13b79513b0f  Mariva Catering Services                   5   
...                         ...                       ...                 ...   
22375  620cd5a6aa28c13b79530d38          Peyton And Byrne                   5   
22418  620cd5a7aa28c13b79530fed                      Pure                   5   
22432  620cd5a7aa28c13b79531056            Railhouse Café                   5   
22468  620cd5a7aa28c13b7953127b               Sainsbury's                   5   
22549  620cd5a7aa28c13b79531683            Sticks'n'Sushi  AwaitingInspection   

                AddressLine2  PostCode  Geocode_Longitude  Geocode_Latitude  \
78                    London   SW6 2GD                NaN               NaN   
139                   London    W6 9JG                NaN               NaN   
187                   London   W14 8XU                NaN               NaN   
454                   London   SW6 2FG                NaN               NaN   
610                   London   SW6 2FR                NaN               NaN   
...                      ...       ...                ...               ...   
22375       49-52 Piccadilly   W1V 9HA                NaN               NaN   
22418    City Of Westminster  SW1E 5DJ                NaN               NaN   
22432    City Of Westminster  SW1E 5DJ                NaN               NaN   
22468  112-120 Brompton Road   SW3 1JJ                NaN               NaN   
22549    City Of Westminster  SW1E 5DJ                NaN               NaN   

      AddressLine3                                            geocode  
78             NaN      (SW6 2GD, (51.46750555, -0.1872712484691929))  
139            NaN  (London Borough of Hammersmith and Fulham, Lon...  
187            NaN  (London Borough of Hammersmith and Fulham, Lon...  
454            NaN                    (SW6 2FG, (51.47412, -0.18297))  
610            NaN  (London Borough of Hammersmith and Fulham, Lon...  
...            ...                                                ...  
22375       London  (City of Westminster, Greater London, England,...  
22418       London  (City of Westminster, Greater London, England,...  
22432       London  (City of Westminster, Greater London, England,...  
22468       London  (City of Westminster, Greater London, England,...  
22549       London  (City of Westminster, Greater London, England,...  

[255 rows x 9 columns]

In [295]:
for i in range(len(mixed_list)):
    print(isinstance(mixed_list[i][1]['geocode'], type(None)))

False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
True
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
True
False
False
False
False
False
False
False
False
False
True
False
True
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
True
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
Fal

In [326]:
#rdata_geonull['geocode']
#Removing None data from the mixed_list list as well
print(f'Before NoneTypes are deleted: {len(mixed_list)}, '\n')

for i in mixed_list:
    if isinstance(i[1]['geocode'], type(None)):
        mixed_list.remove(i)
        
print(f'After NoneTypes are deleted: {len(mixed_list)}')

261 



255

In [328]:
mixed_list #There are no NoneTypes in mixed_list, their respective coordinates will now be extracted and added to the original rdata dataframe!

[(78,
  _id                             620cd586aa28c13b7951316a
  geocode    (SW6 2GD, (51.46750555, -0.1872712484691929))
  Name: 78, dtype: object),
 (139,
  _id                                 620cd586aa28c13b79513296
  geocode    (London Borough of Hammersmith and Fulham, Lon...
  Name: 139, dtype: object),
 (187,
  _id                                 620cd586aa28c13b795133b3
  geocode    (London Borough of Hammersmith and Fulham, Lon...
  Name: 187, dtype: object),
 (454,
  _id               620cd587aa28c13b795137a6
  geocode    (SW6 2FG, (51.47412, -0.18297))
  Name: 454, dtype: object),
 (610,
  _id                                 620cd587aa28c13b79513b0f
  geocode    (London Borough of Hammersmith and Fulham, Lon...
  Name: 610, dtype: object),
 (655,
  _id                                 620cd587aa28c13b79513c08
  geocode    (W6, II, Schönau am Königssee, Landkreis Berch...
  Name: 655, dtype: object),
 (790,
  _id                                 620cd587aa28c13b79513e9c
  ge

In [332]:
mixed_list[0][1]['geocode'].raw

{'place_id': 286845756,
 'licence': 'Data © OpenStreetMap contributors, ODbL 1.0. https://osm.org/copyright',
 'boundingbox': ['51.30750555',
  '51.62750555',
  '-0.34727124846919',
  '-0.027271248469193'],
 'lat': '51.46750555',
 'lon': '-0.1872712484691929',
 'display_name': 'SW6 2GD',
 'class': 'place',
 'type': 'postcode',
 'importance': 0.325,
 'address': {'postcode': 'SW6 2GD', 'country_code': 'gb'}}

In [369]:
coords_dict = {}
for i in mixed_list:
    #print(i[1]['geocode'].raw['lat'])
    coords_dict[i[0]] = (float(i[1]['geocode'].raw['lat']), float(i[1]['geocode'].raw['lon']))

In [370]:
print(len(coords_dict))
geocoded_rows_with_coords = pd.DataFrame.from_dict(coords_dict).T.rename(columns={0:'Geocode_Latitude', 1:'Geocode_Longitude'})
geocoded_rows_with_coords

255


Geocode_Latitude  Geocode_Longitude
78            51.467506          -0.187271
139           51.492360          -0.230230
187           51.492010          -0.207070
454           51.474120          -0.182970
610           51.475140          -0.186800
...                 ...                ...
22375         51.508014          -0.139312
22418         51.497418          -0.143508
22432         51.497418          -0.143508
22468         51.499497          -0.164454
22549         51.497418          -0.143508

[255 rows x 2 columns]

In [371]:
rdata_geonull

_id              BusinessName         RatingValue  \
78     620cd586aa28c13b7951316a       Baxterstorey UK Ltd                   5   
139    620cd586aa28c13b79513296                Brown Rice                   5   
187    620cd586aa28c13b795133b3            Chapter Coffee                   5   
454    620cd587aa28c13b795137a6            Harris & Hoole                   5   
610    620cd587aa28c13b79513b0f  Mariva Catering Services                   5   
...                         ...                       ...                 ...   
22375  620cd5a6aa28c13b79530d38          Peyton And Byrne                   5   
22418  620cd5a7aa28c13b79530fed                      Pure                   5   
22432  620cd5a7aa28c13b79531056            Railhouse Café                   5   
22468  620cd5a7aa28c13b7953127b               Sainsbury's                   5   
22549  620cd5a7aa28c13b79531683            Sticks'n'Sushi  AwaitingInspection   

                AddressLine2  PostCode  Geocode_Longitude  Geocode_Latitude  \
78                    London   SW6 2GD                NaN               NaN   
139                   London    W6 9JG                NaN               NaN   
187                   London   W14 8XU                NaN               NaN   
454                   London   SW6 2FG                NaN               NaN   
610                   London   SW6 2FR                NaN               NaN   
...                      ...       ...                ...               ...   
22375       49-52 Piccadilly   W1V 9HA                NaN               NaN   
22418    City Of Westminster  SW1E 5DJ                NaN               NaN   
22432    City Of Westminster  SW1E 5DJ                NaN               NaN   
22468  112-120 Brompton Road   SW3 1JJ                NaN               NaN   
22549    City Of Westminster  SW1E 5DJ                NaN               NaN   

      AddressLine3                                            geocode  
78             NaN      (SW6 2GD, (51.46750555, -0.1872712484691929))  
139            NaN  (London Borough of Hammersmith and Fulham, Lon...  
187            NaN  (London Borough of Hammersmith and Fulham, Lon...  
454            NaN                    (SW6 2FG, (51.47412, -0.18297))  
610            NaN  (London Borough of Hammersmith and Fulham, Lon...  
...            ...                                                ...  
22375       London  (City of Westminster, Greater London, England,...  
22418       London  (City of Westminster, Greater London, England,...  
22432       London  (City of Westminster, Greater London, England,...  
22468       London  (City of Westminster, Greater London, England,...  
22549       London  (City of Westminster, Greater London, England,...  

[255 rows x 9 columns]

In [373]:
#Checking if the indexes of the dataframes are the same
[j for j in geocoded_rows_with_coords.index ] == [j for j in rdata_geonull.index]

True

In [374]:
#dropping these columns(Geocode_Longitude and Geocode_Latitude) so that they can be replaced by the new ones with the geocoded values
rdata_geonull = rdata_geonull.drop(['Geocode_Longitude', 'Geocode_Latitude'], axis=1)
rdata_geonull

_id              BusinessName         RatingValue  \
78     620cd586aa28c13b7951316a       Baxterstorey UK Ltd                   5   
139    620cd586aa28c13b79513296                Brown Rice                   5   
187    620cd586aa28c13b795133b3            Chapter Coffee                   5   
454    620cd587aa28c13b795137a6            Harris & Hoole                   5   
610    620cd587aa28c13b79513b0f  Mariva Catering Services                   5   
...                         ...                       ...                 ...   
22375  620cd5a6aa28c13b79530d38          Peyton And Byrne                   5   
22418  620cd5a7aa28c13b79530fed                      Pure                   5   
22432  620cd5a7aa28c13b79531056            Railhouse Café                   5   
22468  620cd5a7aa28c13b7953127b               Sainsbury's                   5   
22549  620cd5a7aa28c13b79531683            Sticks'n'Sushi  AwaitingInspection   

                AddressLine2  PostCode AddressLine3  \
78                    London   SW6 2GD          NaN   
139                   London    W6 9JG          NaN   
187                   London   W14 8XU          NaN   
454                   London   SW6 2FG          NaN   
610                   London   SW6 2FR          NaN   
...                      ...       ...          ...   
22375       49-52 Piccadilly   W1V 9HA       London   
22418    City Of Westminster  SW1E 5DJ       London   
22432    City Of Westminster  SW1E 5DJ       London   
22468  112-120 Brompton Road   SW3 1JJ       London   
22549    City Of Westminster  SW1E 5DJ       London   

                                                 geocode  
78         (SW6 2GD, (51.46750555, -0.1872712484691929))  
139    (London Borough of Hammersmith and Fulham, Lon...  
187    (London Borough of Hammersmith and Fulham, Lon...  
454                      (SW6 2FG, (51.47412, -0.18297))  
610    (London Borough of Hammersmith and Fulham, Lon...  
...                                                  ...  
22375  (City of Westminster, Greater London, England,...  
22418  (City of Westminster, Greater London, England,...  
22432  (City of Westminster, Greater London, England,...  
22468  (City of Westminster, Greater London, England,...  
22549  (City of Westminster, Greater London, England,...  

[255 rows x 7 columns]

In [375]:
merged = rdata_geonull.merge(geocoded_rows_with_coords, left_index=True, right_index=True, how='inner')
merged

_id              BusinessName         RatingValue  \
78     620cd586aa28c13b7951316a       Baxterstorey UK Ltd                   5   
139    620cd586aa28c13b79513296                Brown Rice                   5   
187    620cd586aa28c13b795133b3            Chapter Coffee                   5   
454    620cd587aa28c13b795137a6            Harris & Hoole                   5   
610    620cd587aa28c13b79513b0f  Mariva Catering Services                   5   
...                         ...                       ...                 ...   
22375  620cd5a6aa28c13b79530d38          Peyton And Byrne                   5   
22418  620cd5a7aa28c13b79530fed                      Pure                   5   
22432  620cd5a7aa28c13b79531056            Railhouse Café                   5   
22468  620cd5a7aa28c13b7953127b               Sainsbury's                   5   
22549  620cd5a7aa28c13b79531683            Sticks'n'Sushi  AwaitingInspection   

                AddressLine2  PostCode AddressLine3  \
78                    London   SW6 2GD          NaN   
139                   London    W6 9JG          NaN   
187                   London   W14 8XU          NaN   
454                   London   SW6 2FG          NaN   
610                   London   SW6 2FR          NaN   
...                      ...       ...          ...   
22375       49-52 Piccadilly   W1V 9HA       London   
22418    City Of Westminster  SW1E 5DJ       London   
22432    City Of Westminster  SW1E 5DJ       London   
22468  112-120 Brompton Road   SW3 1JJ       London   
22549    City Of Westminster  SW1E 5DJ       London   

                                                 geocode  Geocode_Latitude  \
78         (SW6 2GD, (51.46750555, -0.1872712484691929))         51.467506   
139    (London Borough of Hammersmith and Fulham, Lon...         51.492360   
187    (London Borough of Hammersmith and Fulham, Lon...         51.492010   
454                      (SW6 2FG, (51.47412, -0.18297))         51.474120   
610    (London Borough of Hammersmith and Fulham, Lon...         51.475140   
...                                                  ...               ...   
22375  (City of Westminster, Greater London, England,...         51.508014   
22418  (City of Westminster, Greater London, England,...         51.497418   
22432  (City of Westminster, Greater London, England,...         51.497418   
22468  (City of Westminster, Greater London, England,...         51.499497   
22549  (City of Westminster, Greater London, England,...         51.497418   

       Geocode_Longitude  
78             -0.187271  
139            -0.230230  
187            -0.207070  
454            -0.182970  
610            -0.186800  
...                  ...  
22375          -0.139312  
22418          -0.143508  
22432          -0.143508  
22468          -0.164454  
22549          -0.143508  

[255 rows x 9 columns]

In [382]:
#Adding the merged dataframe to the original rdata dataframe
[idx for idx in rdata[rdata['Geocode_Longitude'].isnull()].index] == merged.index

array([ True,  True,  True,  True,  True,  True,  True,  True,  True,
        True,  True,  True,  True,  True,  True,  True,  True,  True,
        True,  True,  True,  True,  True,  True,  True,  True,  True,
        True,  True,  True,  True,  True,  True,  True,  True,  True,
        True,  True,  True,  True,  True,  True,  True,  True,  True,
        True,  True,  True,  True,  True,  True,  True,  True,  True,
        True,  True,  True,  True,  True,  True,  True,  True,  True,
        True,  True,  True,  True,  True,  True,  True,  True,  True,
        True,  True,  True,  True,  True,  True,  True,  True,  True,
        True,  True,  True,  True,  True,  True,  True,  True,  True,
        True,  True,  True,  True,  True,  True,  True,  True,  True,
        True,  True,  True,  True,  True,  True,  True,  True,  True,
        True,  True,  True,  True,  True,  True,  True,  True,  True,
        True,  True,  True,  True,  True,  True,  True,  True,  True,
        True,  True,

In [383]:
#Since  the rows in the original dataset match the ones in the merged dataset,and 
#the geocoded coords in the original dataframe are empty, they can be dropped and 
#replaced with the new geocoded rows in the merged dataframe
print(f'Before dropping cols: {len(rdata)}\n')
rdata = rdata.drop([idx for idx in rdata[rdata['Geocode_Longitude'].isnull()].index], axis=0)
print(f"After dropping cols: {len(rdata)}")

Before dropping cols: 22288

After dropping cols: 22033


In [387]:
#rdata = pd.concat([rdata, merged], axis=0)
rdata = pd.concat([rdata, merged], axis=0)

_id          BusinessName         RatingValue  \
0      620cd586aa28c13b79512f6f      101 Thai Kitchen                   3   
1      620cd586aa28c13b79512f75    2020 Mezza & Grill  AwaitingInspection   
2      620cd586aa28c13b79512f78  222 Vegan Restaurant                   3   
3      620cd586aa28c13b79512f7b    24 / 7 Supermarket                   3   
4      620cd586aa28c13b79512f7e            696 Mangal                   5   
...                         ...                   ...                 ...   
22375  620cd5a6aa28c13b79530d38      Peyton And Byrne                   5   
22418  620cd5a7aa28c13b79530fed                  Pure                   5   
22432  620cd5a7aa28c13b79531056        Railhouse Café                   5   
22468  620cd5a7aa28c13b7953127b           Sainsbury's                   5   
22549  620cd5a7aa28c13b79531683        Sticks'n'Sushi  AwaitingInspection   

                AddressLine2  PostCode  Geocode_Longitude  Geocode_Latitude  \
0                     London    W6 0RX          -0.244311         51.493618   
1                     London    W6 9PL          -0.222939         51.488278   
2                     London   W14 9NU          -0.202997         51.485879   
3                     London    W6 0QU          -0.232831         51.492834   
4                     London   SW6 5SA          -0.206834         51.474724   
...                      ...       ...                ...               ...   
22375       49-52 Piccadilly   W1V 9HA          -0.139312         51.508014   
22418    City Of Westminster  SW1E 5DJ          -0.143508         51.497418   
22432    City Of Westminster  SW1E 5DJ          -0.143508         51.497418   
22468  112-120 Brompton Road   SW3 1JJ          -0.164454         51.499497   
22549    City Of Westminster  SW1E 5DJ          -0.143508         51.497418   

      AddressLine3                                            geocode  
0              NaN                                                NaN  
1              NaN                                                NaN  
2              NaN                                                NaN  
3              NaN                                                NaN  
4              NaN                                                NaN  
...            ...                                                ...  
22375       London  (City of Westminster, Greater London, England,...  
22418       London  (City of Westminster, Greater London, England,...  
22432       London  (City of Westminster, Greater London, England,...  
22468       London  (City of Westminster, Greater London, England,...  
22549       London  (City of Westminster, Greater London, England,...  

[22288 rows x 9 columns]

In [388]:
rdata.drop(['geocode'], axis=1, inplace=True)
rdata.head()

_id          BusinessName         RatingValue  \
0  620cd586aa28c13b79512f6f      101 Thai Kitchen                   3   
1  620cd586aa28c13b79512f75    2020 Mezza & Grill  AwaitingInspection   
2  620cd586aa28c13b79512f78  222 Vegan Restaurant                   3   
3  620cd586aa28c13b79512f7b    24 / 7 Supermarket                   3   
4  620cd586aa28c13b79512f7e            696 Mangal                   5   

  AddressLine2 PostCode  Geocode_Longitude  Geocode_Latitude AddressLine3  
0       London   W6 0RX          -0.244311         51.493618          NaN  
1       London   W6 9PL          -0.222939         51.488278          NaN  
2       London  W14 9NU          -0.202997         51.485879          NaN  
3       London   W6 0QU          -0.232831         51.492834          NaN  
4       London  SW6 5SA          -0.206834         51.474724          NaN

In [391]:
rdata = rdata.drop(['AddressLine3'], axis=1) #dropping this column as it isnt needed

In [394]:
rdata.to_csv('rdata.csv', index=False)